In [1]:
import os

os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [2]:
from monty.serialization import loadfn, dumpfn
from ase.filters import FrechetCellFilter
from ase.optimize import LBFGS
from pymatgen.io.ase import AseAtomsAdaptor
from fairchem.core import pretrained_mlip, FAIRChemCalculator
from doped.chemical_potentials import CompetingPhases
from pymatgen.entries.computed_entries import ComputedEntry
from doped.chemical_potentials import CompetingPhasesAnalyzer

/home/atshaam/miniconda3/envs/proj_env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
MODEL = "uma"

In [4]:
supercell_size = 10.1

In [5]:
uma_ff = pretrained_mlip.get_predict_unit("uma-m-1p1", device="cuda")
uma_calc = FAIRChemCalculator(uma_ff, task_name="omat")

In [6]:
MODELS = {
    "uma":uma_calc,
}

In [7]:
def relax_structure(structure): # takes in pymatgen structure
    atoms = structure.to_ase_atoms()
    atoms.calc = MODELS[MODEL]
    
    opt = LBFGS(FrechetCellFilter(atoms))# Delete this FrechetCellFilter when doing the defect structures, need FrechetCellFilter when doing competing phases
    opt.run(0.01, 1000)
    
    relaxed_structure = AseAtomsAdaptor.get_structure(atoms)
    energy = atoms.get_potential_energy()

    return relaxed_structure, energy 

In [8]:
calculated_entries = {}

def calc_competing_phase(comp, dopant): # Pass in formula of species
    cp = CompetingPhases(composition=comp, extrinsic=dopant, energy_above_hull=0.05)
    
    entries = []
    for entry in cp.entries:
        key =  entry.data['material_id'] + entry.structure.composition.reduced_formula
        
        if key in calculated_entries:
            new_entry = calculated_entries[key]
        else:
            try:
                relaxed_structure, energy = relax_structure(entry.structure)
            except ValueError as e:
                print(f"Skipping structure due to error: {e}")
                continue
            new_entry = ComputedEntry(
                relaxed_structure.composition,
                energy, 
                data = {'material_id':entry.data['material_id']}
            )
            calculated_entries[key] = new_entry 
        entries.append(new_entry)
    return cp, entries 

In [9]:
def calc_competing_phase_analysis(comp, entries):
    
    cpa = CompetingPhasesAnalyzer(composition=comp, entries=entries)
    
    return cpa.chempots, cpa.unstable_host

In [10]:
relaxed_defect = loadfn(f'../../data/{MODEL}/relaxed_supercell_tm.json')

In [ ]:
done = []

In [ ]:
for key, val in relaxed_defect.items():
    if key not in done:
        formula = relaxed_defect[key]['formula']
        dopant = relaxed_defect[key]['dopant']
        print(formula, dopant, key)
        cp, entries = calc_competing_phase(formula, dopant) # do you have to return cp?
        chem_pot, unstable = calc_competing_phase_analysis(formula, entries)
        if 'competing phases' not in relaxed_defect[key]:
            relaxed_defect[key]['competing phases'] = {}
        relaxed_defect[key]['competing phases']['chemical potentials'] = chem_pot
        relaxed_defect[key]['competing phases']['entries'] = entries
        relaxed_defect[key]['competing phases']['unstable'] = unstable
        done.append(key)

MgH2Cl2O Mn mp-24337Mn
       Step     Time          Energy          fmax
LBFGS:    0 11:10:43     -103.231556        0.065297
LBFGS:    1 11:10:43     -103.231878        0.038156
LBFGS:    2 11:10:44     -103.232344        0.056498
LBFGS:    3 11:10:44     -103.233732        0.096963
LBFGS:    4 11:10:45     -103.235100        0.106153
LBFGS:    5 11:10:45     -103.236116        0.061521
LBFGS:    6 11:10:45     -103.236633        0.050477
LBFGS:    7 11:10:46     -103.237141        0.045664
LBFGS:    8 11:10:46     -103.237835        0.080225
LBFGS:    9 11:10:46     -103.238563        0.080418
LBFGS:   10 11:10:47     -103.239014        0.039359
LBFGS:   11 11:10:47     -103.239210        0.029083
LBFGS:   12 11:10:48     -103.239351        0.028438
LBFGS:   13 11:10:48     -103.239561        0.050799
LBFGS:   14 11:10:48     -103.239851        0.058947
LBFGS:   15 11:10:49     -103.240211        0.046995
LBFGS:   16 11:10:49     -103.240679        0.055323
LBFGS:   17 11:10:50     

logm result may be inaccurate, approximate err = 2.223492068521543e-13


LBFGS:   13 11:12:56     -162.902861        0.050850
LBFGS:   14 11:12:56     -162.904121        0.065749
LBFGS:   15 11:12:57     -162.905970        0.089081
LBFGS:   16 11:12:57     -162.908299        0.087031
LBFGS:   17 11:12:58     -162.910473        0.063436
LBFGS:   18 11:12:58     -162.911835        0.050737
LBFGS:   19 11:12:59     -162.912556        0.048949


logm result may be inaccurate, approximate err = 2.2368995501993917e-13


LBFGS:   20 11:12:59     -162.913145        0.050848
LBFGS:   21 11:13:00     -162.914030        0.052592
LBFGS:   22 11:13:00     -162.915318        0.065045
LBFGS:   23 11:13:01     -162.916834        0.072163


...

LBFGS:   60 17:51:06     -323.820583        0.028965


logm result may be inaccurate, approximate err = 4.225939604622833e-13


LBFGS:   61 17:51:06     -323.820956        0.021299


logm result may be inaccurate, approximate err = 4.1946674731444164e-13


LBFGS:   62 17:51:07     -323.821202        0.019536


In [ ]:
dumpfn(relaxed_defect, f'../../data/{MODEL}/relaxed_cp_defect_tm.json')